## Introduction to Scientific Computing
### Lecture 05: Introduction to Data Visualization with Matplotlib
#### J.R. Gladden, Spring 2018, Univ. of Mississippi

Matplotlib has become a robust and industry standard library for plotting in Python. Since we are working here in a Ipython notebook, we can use the %matplolib "magic" to display the graphical output on the browser page (inline), or popup in external windows using a variety of graphical backends (osx, gtk, qt, ...),

In [2]:
%matplotlib wx

In [3]:
import numpy as np
import matplotlib.pyplot as plt


# Define a few functions to plot:

def expdecay(x,lam=1.,A=1.):
    return A*np.exp(-x*lam)

def dampedsine(x,lam=1.,k=1.,A=1.):
    apass=A
    lampass=lam
    return expdecay(x,lam=lampass,A=apass)*np.sin(k*x)

def gauss(x,A=1.,sig=1.,x0=5.):
    return A*np.exp(-(x-x0)**2/sig)

#Lets close any open windows:
plt.close('all')


# Now create an array of x values

x=np.arange(0,10,0.02)

# Make the first plot using a green line 
plt.plot(x,dampedsine(x,lam=0.4,k=10),'g-')
plt.title("A damped sine curve")
plt.xlabel("Time (s)")
plt.ylabel("Amplitude (m)")
#Won't pop up until you tell it to:
plt.show()


We can add a second curve by simply adding another plot command. Note we adding 2 new curves here.

In [4]:
plt.plot(x,expdecay(x,lam=0.4),'b--')
plt.plot(x,-expdecay(x,lam=0.4),'b--')

In [5]:
plt.figure(1)
plt.plot(x,np.sin(10*x))

plt.figure(2,figsize=(12,8)) #(size in inches wide,high)
plt.plot(x,dampedsine(x,k=10)*gauss(x))

#Make figure 1 active and save it to a file
plt.figure(1)
plt.savefig('test.png')

plt.show()

Plotting multiple data sets. We're also are adding a legend - note how we are dynamically updating the legend text based on the current parameters.

In [8]:
t=np.linspace(0,10,100)
def V(t,RC):    
   return 10*np.exp(-t/RC)
RCvals=[0.1,1.0,2.0,4.0,10.0]
markers=['o','s','^','+','D']
for i in range(len(RCvals)):
    marker=markers[i]    
    RC=RCvals[i]    
    plt.plot(t,V(t,RC),'b-'+marker, label='RC=%2.1f'%RC)
plt.legend(loc=1)
plt.xlabel('Time (s)', fontsize=16)
plt.ylabel('Potential (V)',fontsize=16)
plt.show()

Best to use two different axes if your data sets have a large difference in scales.

In [33]:
plt.close('all')
x=np.linspace(0,10,100)
y1=np.sqrt(x)
y2=x**3
plt.plot(x,y1,'g-',lw=2,label='Sqrt(x)')
plt.ylabel('Sqrt(x)')
plt.legend(loc=2)
ax2=plt.twinx()
plt.plot(x,y2,'b--',lw=2,label='x^3')
plt.ylabel('x^3')
plt.xlabel('x')
plt.legend(loc=4)
plt.show()

This is how you do subplots. The subplot triple number (like 221) means a subplot 2x2 grid and the next plot command will go to the 1st plot in the grid.

In [6]:
x=np.linspace(-np.pi,np.pi,100)
plt.subplot(221)
plt.plot(x,np.sin(x))
plt.xlabel('X')
plt.ylabel('Sin(x)')
plt.subplot(222)
plt.plot(x,np.cos(x))
plt.xlabel('X')
plt.ylabel('Cos(x)')
plt.subplot(223)
plt.plot(x,np.tan(x))
plt.xlabel('X')
plt.ylabel('Tan(x)')
plt.subplot(224)
plt.plot(x,np.cosh(x))
plt.xlabel('X')
plt.ylabel('Cosh(x)')
plt.show()

** Fancy Stuff:** Adding arrows, add text annotations, even Latex equations!

In [7]:
plt.close('all')
x=np.linspace(0,np.pi,100)
plt.fill_between(x,np.tan(x),y2=0,lw=2,color='green')
plt.annotate('A pole',xy=(np.pi/2.0,50), xytext=(0.25,10), 
             fontsize=16,arrowprops=dict(facecolor='blue',shrink=0.05))
plt.text(2,40,'$\int_0^\pi \mathrm{tan}(x) = 0$',fontsize=25)
plt.show()

** Polar Plots: ** 

In [8]:
theta=np.arange(0,2*np.pi,np.pi/100)
r1=3+np.sin(4*theta)
r2=3+np.sin(6*theta)
plt.polar(theta,r1)
plt.polar(theta,r2)
plt.show()

** Quiver (Vector) Plots: ** These are 2D plots of a vector field.  So every point in the 2D space needs to have a vector (magnitude and direction) associated with it.  This requires generating a 'meshgrid' in the 2D space.  Also take care about the length of the vectors since they can vary wildly and obscure the story you are trying to tell.

In [19]:
plt.close('all')
gridvec=np.linspace(0,2*np.pi,50) 
x,y=np.meshgrid(gridvec,gridvec) # Make a uniform square mesh of 2D points.  Outputs 2 2D arrays.
U=np.sin(y) # function for the 'x' component of the vector
V=np.cos(x) # function for the 'y' component
plt.quiver(x,y,U,V,np.sqrt(U**2+V**2)) # The last argument scales the color by the magnitude.
plt.title('Vector (quiver) plot of V_x=sin(x), V_y=cos(y)', fontsize=20)
plt.xlabel('x',fontsize=20)
plt.ylabel('y',fontsize=20)

In [14]:
plt.quiver?

** Interacting with plots: ** Matplotlib does provide tools for interacting with plots to make them more dynamic.  This requires capturing an 'event' (such as a click, button press, or mouse movment) and adjusting something on the plot when that event occurs.  This is rather basic "event handling" but sufficient for a lot of what we do as scientists.  This example plots a bunch of gaussians centered on where a user clicks in the plot area.  It also takes in some button clicks to clear of quit (and close the window).  ** NOTE: **  This **sometimes** works in the iPython notebook, but should work fine when run in Canopy or directly in the iPython command line.

In [28]:
plt.close('all')


def click(event):
    col=(np.random.rand(),np.random.rand(),np.random.rand())   #set a random RGB tuple for the current curve color
    #OR could use: col=tuple(rand(3))
    xClick,yClick= event.xdata, event.ydata  # grab the x,y coordinates of the click (floats)
    plt.plot(x,gauss(x,A=yClick,x0=xClick),color=col)
    plt.draw()

def done(event1):
    if event1.key == 'q': close('all')  
    if event1.key == 'c': 
        plt.clf()
        plt.plot([0],[0])        #clears existing graphs
        plt.axis([0, 10, 0, 1])
        plt.draw()
# Define x values
x=np.linspace(0,10,100)
#now register the event to the above function
cid = plt.connect('button_press_event',click)
cid1= plt.connect('key_press_event',done)

plt.title("Click anywhere in the graph to draw a new Gaussian.  \n Type 'q' to quit")
plt.xlabel("X")
plt.ylabel("Y")
plt.plot([0],[0])        #clears existing graphs
plt.axis([min(x), max(x), 0, 1])
plt.show()

AttributeError: 'module' object has no attribute 'random'